# Hyperbolic equations 1

* Consider equations with only convection

$$\frac{\partial f}{\partial t} + u\frac{\partial f}{\partial x} = 0.$$

* Assume constant $u$.
* This is a linear PDE.
* **Exact solution**

$$f(x,t) = f_0(x-ut),$$

where $f_0(x)$ is the initial $f$ profile. That is, we just shift the domain. This is consistent with this PDE being a *wave* equation, where the solution *convects* across the domain without changing shape.

### Note
* The second order wave equation is given by 

$$\frac{\partial^2f}{\partial^2 t} = u^2\frac{\partial^2f}{\partial^2 x}.$$

* Consider the following system of two first order wave equations:

$$f_t + ug_x = 0 \xrightarrow{\partial/\partial t} f_{tt} + ug_{xt} = 0$$

$$g_t + uf_x = 0 \xrightarrow[*u,\text{ swap xt order}]{\partial/\partial x} ug_{tx} + u^2f_{xx} = 0$$

* Now subtract the second equation from the first to recover the second order wave equation:

$$f_{tt} - u^2f_{xx} = 0.$$

* This shows that the second order wave equation is equivalent to a system of two first order wave equations.
* Here, we'll focus on the first order wave equation.

## Methods
* FTCS
* Lax
* Lax Wendroff
* MacCormack
* Upwind
* BTCS

### <font color='red'>FTCS</font>

$$f_t + uf_x = 0,$$

$$\frac{f_i^{n+1}-f_i^n}{\Delta t} + u\frac{f_{i-1}^n-f_{i+1}^n}{2\Delta x} = 0,$$

$$f_i^{n+1} = f_i^n - \frac{c}{2}(f_{i+1}^n-f_{i-1}^n).$$

* $c=u\Delta t/\Delta x$
* $\mathcal{O}(\Delta t)$
* $\mathcal{O}(\Delta x^2)$
* **unconditionally unstable**
* Consistent
* Stencil:

```
    *     O     *
    
    O     O     O
```




### <font color='red'>Lax</font>

* Fix the instability.
* Instead of $f_i^n$ use $\frac{1}{2}(f_{i-1}^n + f_{i+1}^n).$

$$f_i^{n+1} = \frac{1}{2}(f_{i-1}^n+f_{i+1}^n) - \frac{u}{2}(f_{i+1}^n-f_{i-1}^n).$$

* $\mathcal{O}(\Delta t)$
* $\mathcal{O}(\Delta x^2)$
* Stable for $c=\frac{u\Delta t}{\Delta x}\le 1$
    * $c\le 1$ is the Courant Friedrichs Lewy (CFL) stability criterion
* **Inconsistent**

```
    *     O     *
    
    O     *     O
```



### Lax Wendroff

* Fix the FTCS method
* Consider the modified differential equation: MDE
    * When we solve PDEs as finite difference equations (FDEs), the FDE has truncation error (from terms we ignore in the Taylor series).
    * A Taylor series can be used to show the PDE that is *equivalent* to the FDE we are solving. This equivalent PDE is called the modified differential equation (MDE).
* PDE:

$$f_t + uf_x = 0.$$

* FTCS:

$$\frac{f_i^{n+1}-f_i^n}{\Delta t} + \frac{c}{2\Delta t}(f_{i-1}^n-f_{i+1}^n) = 0.$$

* Taylor series for $f$'s:

$$ f_i^{n+1} = f_i^n + \Delta t f_t + \frac{1}{2}\Delta t^2f_{tt} + \ldots,$$
$$ f_{i-1}^{n} = f_i^n - \Delta x f_x + \frac{1}{2}\Delta x^2f_{xx} + \ldots,$$
$$ f_{i+1}^{n} = f_i^n + \Delta x f_x + \frac{1}{2}\Delta x^2f_{xx} + \ldots,$$

* Substitute this into FTCS to get the MDE:

$$f_t + uf_x = -\frac{1}{2}\Delta tf_{tt} + (\text{higher order terms}).$$

* Now, the $f_{tt}$ term in this equation can be replaced with $u^2f_{xx}$ as follows:

$$\frac{\partial}{\partial t}(f_t = -uf_x)\rightarrow f_{tt}=-uf_{tx} = -u(f_t)_x = u^2f_{xx}.$$

* In the last step, we used $f_t = -uf_x$.
* Hence, the MDE is:

<font color='blue'>
$$f_t + uf_x = \underbrace{-\frac{1}{2}\Delta t u^2f_{xx}}_{\text{error term}}.$$
</font>

* Now, subtract off the error term from the RHS of FTCS:

$$\frac{f_i^{n+1}-f_i^n}{\Delta t} + \frac{c}{2\Delta t}(f_{i+1}^n-f_{i-1}^n) = \frac{1}{2}\Delta tu^2f_{xx}.$$

* Finally, discretize the $f_{xx}$ term and rearrange:

<font color=blue>
$$f_i^{n+1} = f_i^n - \frac{c}{2}(f_{i+1}^n-f_{i-1}^n) + \frac{1}{2}c^2(f_{i-1}^n - 2f_i^n + f_{i+1}^n).$$
</font>

* $\mathcal{O}(\Delta t^2)$
* $\mathcal{O}(\Delta x^2)$
* **Stable** for $c=\frac{u\Delta t}{\Delta x}\le 1$
* **Consistent**
* Stencil:

```
    *     O     *
    
    O     O     O
```

#### Note
* The error terms are now $f_{ttt}$ and $f_{xxx}$ $\rightarrow$ third order derivatives in the error terms.
    * Error terms that have even derivatives (like $f_{xx}$) are diffusive and cause unphysical smoothing in the solution.
    * Error terms that have odd derivatives (like $f_{xxx}$) are dispersive and cause unphysical wiggles in the solution.
    
#### Question
* Normally, diffusive terms help stability, so why is it that the error term in the FTCS method above (which is a second order, diffusive term) is the cause of the instability? 
    * What does this term do physically?
    * Look at the term and consider its form.




## MacCormack

* Was and is widely used
* Used for systems of equations, nonlinear equations
* Similar to Crank-Nicolson

$$\frac{\partial f}{\partial t} = -u\frac{\partial f}{\partial x} = \text{RHS} = F.$$

$$\partial f = F\partial t \xrightarrow{\int} f_i^{n+1}-f_i^n = \int Fdt = \overline{F}dt,$$

where 

$$\overline{F} = \frac{1}{\Delta t}\int_t^{t+\Delta t}Fdt.$$

* $F$ is the slope in time of $f$, so $\overline{F}$ is the average slope.
* Approximate this average slope as 
$$\overline{F} = \frac{1}{2}(F^n+F^{n+1}).$$
* Hence, 
$$f_i^{n+1} = f_i^n +\frac{\Delta t}{2}(F_i^n + F_i^{n+1}).$$

* If we take an explicit Euler step to $\tilde{f}_i^{n+1}$, then we can evaluate $F_i^{n+1}$ there. Then we can evaluate the above equation explicitly.
    * This would be the equivalent of the Modified Euler method for PDEs.
* We do this, *but* 
    * When discretizing $F_i^n$ we use a forward difference: $f_x = (f_{i+1}-f_i)/\Delta x$. Denote this as $^+F_i^{n+1}.$
    * When discretizing $F_i^{n+1}$ we use a backward difference: $f_x = (f_{i}-f_{i-1})/\Delta x$. Denote this as $^-F_i^{n+1}.$

* Summary:
    * Predictor:
    <font color='blue'>
    $$\tilde{f}_i^{n+1} = f_i^n - c(f_{i+1}^n-fi^n),$$
    </font>
    * Corrector:
    <font color='blue'>
    $$f_i^{n+1} = f_i^n - \frac{1}{2}[c(f_{i+1}^n-f_i^n) + c(\tilde{f}_i^{n+1}-\tilde{f}_{i-1}^{n+1})].$$
    </font>
    * This second equation can be written as
    $$f_i^{n+1} = \frac{1}{2}[f_i^n + \tilde{f}_i^{n+1} - c(\tilde{f}_i^{n+1} - \tilde{f}_{i-1}^{n+1})].$$

* For the 1-D linear wave equation, this method is the same as the Lax Wendroff method.
    
* $\mathcal{O}(\Delta t^2)$
* $\mathcal{O}(\Delta x^2)$
* Stable for $c=\frac{u\Delta t}{\Delta x}\le 1$
* Consistent
* Stencil:

```
    O     O     *
    
    *     O     O
```

## Upwind method
* We have seen this already. 
* For positive $u$ we have
$$ f_i^{n+1} = f_i^n - c(f_i^n - f_{i-1}^n).$$

* $\mathcal{O}(\Delta t)$
* $\mathcal{O}(\Delta x)$
* Stable for $c=\frac{u\Delta t}{\Delta x}\le 1$
* Consistent
* Stencil:

```
    *     O     *
    
    O     O     *
```

## Second order upwind 
* If we use our old second order one-sided finite difference approximation for $f_x$, the result is unconditionally unstable.
* Hoffman gives an alternative:

$$f_i^{n+1} = f_i^n - c(f_i^n - f_{i-1}^n) - \frac{c(1-c)}{2}(f_i^n - 2f_{i-1}^n + f_{i-2}^n).$$

* This equation is exact for the linear 1D wave equation for $c=1$.

* $\mathcal{O}(\Delta t^2)$
* $\mathcal{O}(\Delta x^2)$
* Stable for $c=\frac{u\Delta t}{\Delta x}\le 2$
* Consistent
* Stencil:

```
    *     *     O     *
    
    O     O     O     *
```

## <font color='red'> BTCS </font>

$$\frac{f_i^{n+1}-f_i^n}{\Delta t} + \frac{u}{2\Delta x}(f_{i-1}^{n+1}-f_{i-1}^{n+1}) = 0.$$

* $\mathcal{O}(\Delta t)$
* $\mathcal{O}(\Delta x^2)$
* Unconditionally stable
* Consistent
* **Unphysical**: $\infty$ propagation speed of information, **unlike** the PDE.
    * The wave *lags* behind the real answer.
* Stencil:

```
    O     O     O
   
    *     O     *
```


## Methods Summary

|   Method   | Recommend | $\mathcal{O}(\Delta t)$ | $\mathcal{O}(\Delta x)$ | Approach | Stability | Comment |
|:-----------|:---------:|:-----------------------:|:-----------------------:|:---------|:---------:|:--------|
| FTCS       |    X      | 1                       | 2                       | direct, forward in time, central in space | NO | doesn't work |
| Lax       |    X      | 1                       | 2                       | average $f_i^n$          | $c\le 1$ | inconsistent|
| Lax Wendroff |    okay     | 2                       | 2                       | fix low order error $f_{tt}$ term           | $c\le 1$ | hard for nonlinear, systems, multi-D |
| MacCormack |    good     | 2                       | 2                       | time adv. with avg. RHS slope:           | $c\le 1$ | good for nonlinear, systems, multi-D |
| Upwind |    poor     | 1                       | 1                       | very diffusive           | $c\le 1$ | diffusive, low order |
| 2nd Order Upwind |    okay     | 2                       | 2                       | 3 point stencil           | $c\le 2$ | oscillatory |
| BTCS |    okay     | 1                       | 2                       | implicit           | $c\le 2$ | unphysical info. speed |